In [1]:
import tensorflow as tf
from tensorflow import keras
import numpy as np

In [2]:
fashion_mnist = keras.datasets.mnist

(train_images, train_labels), (test_images, test_labels) = fashion_mnist.load_data()
train_shape = train_images.shape
test_shape = test_images.shape

y_shape = len(set(train_labels))

train_images_reshaped = train_images.reshape(train_shape[0],train_shape[1]*train_shape[2])/255.0
test_images_reshaped = test_images.reshape(test_shape[0],train_images_reshaped.shape[1])/255.0

In [3]:
hidden_sizes = [1000,1000,500,200]

In [4]:
tf.reset_default_graph()

with tf.device("/CPU:0"):
    x_placeholder = tf.placeholder(tf.float32,shape = (None,train_shape[1]*train_shape[2]))
    y_placeholder = tf.placeholder(tf.int64,shape=(None))
    weight_prune_k = tf.placeholder(tf.float32,shape = ())
    output_layer_weights =  tf.Variable( tf.truncated_normal([hidden_sizes[-1],y_shape]))


    weights_matrices = []
    layer_outputs = []
    weights_magnitudes_matrices = []
    top_indices_list = []
    prunned_weight_matrices = []
    prunned_layer_outputs = []
    weights_to_prune_matrices = []

    layer_outputs.append(x_placeholder)
    prunned_layer_outputs.append(x_placeholder)

    for layer in range(len(hidden_sizes)):
        if layer == 0:

            prev_units = int(x_placeholder.shape[1]) 
        else:
            prev_units = int(weights_matrices[layer-1].shape[1])

        layer_units = hidden_sizes[layer]

        print(layer+1, (prev_units,layer_units))
        weights_matrix_l = tf.Variable( tf.truncated_normal ([prev_units,layer_units]))
        layer_output =  tf.nn.relu( tf.matmul(layer_outputs[layer],weights_matrix_l))

        layer_total_weights = tf.size(weights_matrix_l)
        layer_weights_to_prune =  tf.cast(tf.floor( 
                                    tf.multiply(tf.cast(layer_total_weights,tf.float32),weight_prune_k)),tf.int32)
        weights_magnitudes = tf.abs(weights_matrix_l)
        top_values, top_indices = tf.nn.top_k(tf.reshape(-weights_magnitudes, (-1,)), layer_weights_to_prune)
        #top_indices = tf.stack(((top_indices // weights_magnitudes.shape[1]), (top_indices % weights_magnitudes.shape[1])), -1)
        top_indices = tf.stack(((top_indices // weights_magnitudes.shape[1]), (top_indices % weights_magnitudes.shape[1])), -1)
        
        with tf.control_dependencies([weights_matrix_l,top_indices]):
        #weights_copy_l = tf.stop_gradient(tf.Variable(tf.identity(weights_matrix_l)))
            #weights_copy_l = tf.Variable(tf.identity(weights_matrix_l),trainable = False)
            weights_copy_l = tf.Variable(weights_matrix_l.read_value(),trainable=False)
            #prunned_weights_l = weights_copy_l 
        #prunned_weights_l = tf.scatter_nd_update(weights_copy_l,[[1,1],[1,2]],[0,0])
        #prunned_weights_l = tf.scatter_nd_update(weights_copy_l,top_indices, tf.zeros(shape=(top_indices.shape[0])))
            tf.Print(top_indices,[top_indices])
            prunned_weights_l = tf.scatter_nd_update(weights_copy_l,top_indices, tf.zeros(shape=(layer_weights_to_prune))) #this one
            prunned_layer_output = tf.nn.relu(tf.matmul(prunned_layer_outputs[layer],prunned_weights_l))
        
        weights_matrices.append(weights_matrix_l)
        layer_outputs.append(layer_output)
        weights_magnitudes_matrices.append(weights_magnitudes)
        top_indices_list.append(top_indices)
        prunned_weight_matrices.append(prunned_weights_l)
        prunned_layer_outputs.append(prunned_layer_output)
        weights_to_prune_matrices.append(layer_weights_to_prune)

    last_layer_output =    tf.matmul(  layer_output , output_layer_weights)
    last_prunned_layer_output = tf.matmul(prunned_layer_output,output_layer_weights)
    last_prunned_layer_soft_output = tf.nn.softmax(last_prunned_layer_output)
    last_prunned_layer_hard_output = tf.argmax(last_prunned_layer_soft_output,axis = 1)

    print(layer+2,  (hidden_sizes[-1],y_shape))

    loss =  tf.reduce_mean(
        tf.nn.sparse_softmax_cross_entropy_with_logits(labels = y_placeholder,logits = last_layer_output))
    optimizer_step = tf.train.AdamOptimizer(0.01).minimize(loss)

    last_layer_hard_output = tf.argmax(last_layer_output,axis=1)
    accuracy = tf.reduce_mean( tf.cast( tf.equal(last_layer_hard_output,y_placeholder),tf.float32))
    prunned_accuracy = tf.reduce_mean(tf.cast(tf.equal(last_prunned_layer_hard_output,y_placeholder),tf.float32))


    init = tf.global_variables_initializer()

W0624 18:23:01.869242 4534027712 deprecation.py:323] From /Users/llealhernandez/anaconda3/envs/tf/lib/python3.7/site-packages/tensorflow/python/ops/variables.py:2618: Variable.initialized_value (from tensorflow.python.ops.variables) is deprecated and will be removed in a future version.
Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.
W0624 18:23:01.876658 4534027712 deprecation.py:323] From <ipython-input-4-c0e4da5fb169>:49: Print (from tensorflow.python.ops.logging_ops) is deprecated and will be removed after 2018-08-20.
Instructions for updating:
Use tf.print instead of tf.Print. Note that tf.print returns a no-output operator that directly prints the output. Outside of defuns or eager mode, this operator will not be executed unless it is directly specified in session.run or used as a control dependency for other operators. This is only a concern in graph mode. Below is an example o

1 (784, 1000)
2 (1000, 1000)
3 (1000, 500)
4 (500, 200)
5 (200, 10)


In [5]:
EPOCHS = 20
PRINT_EVERY = 1

In [6]:
config = tf.ConfigProto(allow_soft_placement = True)
sess = tf.InteractiveSession(config=config)

sess.run(init)
feed_dict = {x_placeholder:train_images_reshaped,y_placeholder:train_labels}

for epoch in range(1,EPOCHS + 1):
    _,epoch_loss,epoch_output,epoch_hard_output,epoch_acc  = sess.run([optimizer_step,loss,last_layer_output,last_layer_hard_output,accuracy],feed_dict)
    
    if epoch % PRINT_EVERY == 0:
        print("Epoch :{} loss:{}  epoch acc:{}".format(epoch,epoch_loss,epoch_acc))
        

trained_weights =  sess.run([layer  for layer in  weights_matrices],feed_dict=feed_dict)


Epoch :1 loss:585887.875  epoch acc:0.06201666593551636
Epoch :2 loss:637186.625  epoch acc:0.16121666133403778
Epoch :3 loss:562563.4375  epoch acc:0.18400000035762787
Epoch :4 loss:325465.78125  epoch acc:0.2878166735172272
Epoch :5 loss:273113.1875  epoch acc:0.37701666355133057
Epoch :6 loss:199126.921875  epoch acc:0.36660000681877136
Epoch :7 loss:116473.734375  epoch acc:0.5045833587646484
Epoch :8 loss:62846.9375  epoch acc:0.642300009727478
Epoch :9 loss:48711.62890625  epoch acc:0.6921833157539368
Epoch :10 loss:51938.78515625  epoch acc:0.6766166687011719
Epoch :11 loss:55918.66796875  epoch acc:0.6569333076477051
Epoch :12 loss:54683.77734375  epoch acc:0.6543833613395691
Epoch :13 loss:47057.43359375  epoch acc:0.6775833368301392
Epoch :14 loss:36201.21484375  epoch acc:0.7224666476249695
Epoch :15 loss:26725.9140625  epoch acc:0.7717333436012268
Epoch :16 loss:20708.01953125  epoch acc:0.8060833215713501
Epoch :17 loss:17979.24609375  epoch acc:0.8221499919891357
Epoch :1

In [7]:
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:0.1}
test_acc = sess.run(accuracy,feed_dict=test_feed_dict)

print("Test acc",test_acc)


Test acc 0.8094


In [8]:
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:0.2}
sess.run(prunned_accuracy,feed_dict=test_feed_dict)

0.4976

In [9]:
layer_to_verify = 0
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:0.00002}
out,i , test_weights_matrices, test_prunned_matrices ,to_prune_count= sess.run([last_prunned_layer_hard_output,top_indices_list[layer_to_verify],weights_matrices[layer_to_verify],prunned_weight_matrices[layer_to_verify],weights_to_prune_matrices[layer_to_verify]],feed_dict=test_feed_dict)


In [10]:
set(out)

{0, 1, 2, 3, 4, 5, 6, 7, 8, 9}

In [11]:
i

array([[ 15, 610],
       [516, 748],
       [124,  11],
       [743, 223],
       [274, 786],
       [295, 399],
       [182, 914],
       [234, 430],
       [ 61, 255],
       [384, 254],
       [505, 584],
       [745, 112],
       [475, 509],
       [102,  22],
       [328, 660]], dtype=int32)

In [12]:
test_weights_matrices

array([[ 0.16394272, -0.9000348 , -0.61544013, ...,  0.27792203,
         0.08372461, -0.7040851 ],
       [-1.1655326 , -1.8660072 ,  0.13701624, ...,  0.28392485,
         1.3334846 , -1.2216235 ],
       [-0.33509976, -1.0681643 , -0.08901243, ..., -0.858398  ,
        -0.9578582 ,  0.00383758],
       ...,
       [ 0.43381488,  0.5074702 , -1.2867489 , ...,  1.5416317 ,
         0.2619577 , -1.2484914 ],
       [ 1.9917047 , -0.8189399 , -0.46023974, ...,  1.608211  ,
         0.44874915,  1.5177811 ],
       [ 1.8199874 ,  0.2860626 ,  0.17398256, ..., -0.45444578,
        -1.0897021 , -0.5439008 ]], dtype=float32)

In [13]:
np.min(np.abs(test_weights_matrices))

4.3349573e-06

In [14]:
test_weights_matrices[40][130]

0.80758584

In [15]:
test_prunned_matrices

array([[ 0.        , -0.9000348 , -0.61544013, ...,  0.27792203,
         0.        , -0.7040851 ],
       [-1.1655326 , -1.8660072 ,  0.        , ...,  0.28392485,
         1.3334846 , -1.2216235 ],
       [-0.33509976, -1.0681643 ,  0.        , ..., -0.858398  ,
        -0.9578582 ,  0.        ],
       ...,
       [ 0.43381488,  0.5074702 , -1.2867489 , ...,  1.5416317 ,
         0.2619577 , -1.2484914 ],
       [ 1.9917047 , -0.8189399 , -0.46023974, ...,  1.608211  ,
         0.44874915,  1.5177811 ],
       [ 1.8199874 ,  0.2860626 ,  0.        , ..., -0.45444578,
        -1.0897021 , -0.5439008 ]], dtype=float32)

In [19]:
equal_matrix = test_weights_matrices == test_prunned_matrices
for i in range(test_weights_matrices.shape[0]):
    for j in range(test_prunned_matrices.shape[1]):
        if not equal_matrix[i][j]  and test_prunned_matrices[i][j] == 0:
            print(i,j, test_weights_matrices[i][j] ,test_prunned_matrices[i][j])



0 0 0.16394272 0.0
0 3 -0.08903705 0.0
0 5 0.124597915 0.0
0 19 -0.09757683 0.0
0 24 -0.20044611 0.0
0 30 0.217557 0.0
0 31 -0.12504862 0.0
0 33 -0.14281951 0.0
0 40 -0.13417155 0.0
0 50 0.094776586 0.0
0 51 0.14446867 0.0
0 55 -0.008948052 0.0
0 56 0.09527889 0.0
0 69 -0.11434347 0.0
0 73 0.18713182 0.0
0 74 -0.1286352 0.0
0 101 0.18932754 0.0
0 102 0.10408831 0.0
0 103 -0.009659204 0.0
0 104 0.1978919 0.0
0 116 -0.07596155 0.0
0 122 0.05795836 0.0
0 126 0.014594804 0.0
0 132 0.07731048 0.0
0 133 0.24081135 0.0
0 143 -0.21755247 0.0
0 145 -0.12676169 0.0
0 160 -0.15605801 0.0
0 167 -0.002257889 0.0
0 170 -0.112923 0.0
0 175 0.21454753 0.0
0 182 0.0061068865 0.0
0 185 -0.14694859 0.0
0 187 -0.19296949 0.0
0 190 0.13702507 0.0
0 192 0.22152111 0.0
0 194 -0.04865854 0.0
0 196 0.07774929 0.0
0 197 -0.008760445 0.0
0 200 -0.15959084 0.0
0 202 0.10387898 0.0
0 208 0.08904087 0.0
0 212 0.17217968 0.0
0 219 0.117841505 0.0
0 226 -0.0139172 0.0
0 233 0.06855452 0.0
0 237 -0.060685672 0.0
0 240

3 326 0.15483873 0.0
3 328 0.14320728 0.0
3 329 -0.11417763 0.0
3 332 -0.20993471 0.0
3 334 0.03389444 0.0
3 340 -0.15370801 0.0
3 346 0.21199906 0.0
3 347 0.190392 0.0
3 348 0.014918093 0.0
3 350 -0.04122854 0.0
3 351 -0.22087249 0.0
3 358 -0.017010903 0.0
3 361 0.16377512 0.0
3 377 0.02075735 0.0
3 380 -0.13758874 0.0
3 382 -0.1936328 0.0
3 385 -0.058368575 0.0
3 391 -0.024661634 0.0
3 401 -0.20505357 0.0
3 403 -0.1516394 0.0
3 406 0.02401893 0.0
3 411 0.19563879 0.0
3 415 0.07689843 0.0
3 416 -0.18668945 0.0
3 423 -0.050400127 0.0
3 425 -0.18397139 0.0
3 439 0.24022827 0.0
3 440 -0.0063814283 0.0
3 442 -0.08242835 0.0
3 449 -0.14160872 0.0
3 454 0.23496044 0.0
3 457 0.18079649 0.0
3 459 -0.010053952 0.0
3 463 -0.09696099 0.0
3 464 -0.154794 0.0
3 480 -0.07043086 0.0
3 484 -0.041484684 0.0
3 490 -0.1702905 0.0
3 495 -0.07856339 0.0
3 496 -0.19817142 0.0
3 499 0.23355445 0.0
3 503 0.12031168 0.0
3 510 -0.03865767 0.0
3 512 -0.2216648 0.0
3 516 0.13124385 0.0
3 522 -0.14547418 0.0
3 52

6 104 -0.14546257 0.0
6 109 0.14069983 0.0
6 110 0.030622052 0.0
6 135 0.08121415 0.0
6 137 0.17186627 0.0
6 139 0.089390464 0.0
6 148 0.0768707 0.0
6 155 -0.22875698 0.0
6 162 0.096407056 0.0
6 163 -0.06527285 0.0
6 172 0.1687173 0.0
6 182 0.055282086 0.0
6 184 0.15704563 0.0
6 185 -0.1708929 0.0
6 186 -0.009543984 0.0
6 203 0.06746738 0.0
6 208 0.13951729 0.0
6 211 -0.17616875 0.0
6 217 -0.14130805 0.0
6 218 -0.13233499 0.0
6 225 -0.09609089 0.0
6 226 -0.13857166 0.0
6 243 0.13392788 0.0
6 245 0.01605532 0.0
6 246 -0.079683974 0.0
6 249 0.0027945875 0.0
6 250 0.023382667 0.0
6 262 -0.23866384 0.0
6 263 0.16299883 0.0
6 269 0.20233335 0.0
6 273 0.12148423 0.0
6 276 -0.24175128 0.0
6 277 -0.016641296 0.0
6 279 0.16600166 0.0
6 284 -0.12964833 0.0
6 297 0.14856829 0.0
6 298 0.0151385395 0.0
6 299 0.12979807 0.0
6 304 -0.067003086 0.0
6 310 0.12334133 0.0
6 319 -0.07600089 0.0
6 320 0.14361295 0.0
6 321 -0.08874205 0.0
6 326 0.1173829 0.0
6 328 0.13070837 0.0
6 329 0.03462714 0.0
6 330 -

9 774 0.05631748 0.0
9 777 -0.035594404 0.0
9 788 0.19468434 0.0
9 791 -0.07803944 0.0
9 792 0.1186162 0.0
9 794 -0.032455277 0.0
9 802 0.1376997 0.0
9 807 0.14662555 0.0
9 809 -0.17624605 0.0
9 814 -0.07490998 0.0
9 817 0.22765511 0.0
9 822 0.00013370923 0.0
9 823 -0.14067432 0.0
9 824 0.009465089 0.0
9 827 0.0621257 0.0
9 829 -0.06327253 0.0
9 830 0.016516825 0.0
9 836 -0.1830685 0.0
9 847 0.21301067 0.0
9 850 0.054634072 0.0
9 852 0.040519718 0.0
9 855 0.16820443 0.0
9 857 -0.0730271 0.0
9 859 -0.13218655 0.0
9 867 0.20930997 0.0
9 877 0.12665382 0.0
9 880 -0.02010781 0.0
9 884 0.18269172 0.0
9 886 0.17656602 0.0
9 895 -0.028170493 0.0
9 896 -0.026832039 0.0
9 897 0.11830704 0.0
9 907 -0.12058413 0.0
9 913 -0.16863139 0.0
9 918 -0.20413208 0.0
9 919 0.23499992 0.0
9 926 0.06610108 0.0
9 930 0.030564778 0.0
9 933 -0.09488152 0.0
9 946 -0.03449722 0.0
9 959 -0.16951327 0.0
9 961 0.13880059 0.0
9 964 -0.018641982 0.0
9 971 -0.014319782 0.0
9 974 0.060602438 0.0
9 975 0.11753128 0.0
9 9

13 334 0.008252266 0.0
13 337 0.0964723 0.0
13 339 -0.21478544 0.0
13 347 0.21486533 0.0
13 350 -0.11530269 0.0
13 355 -0.12533718 0.0
13 364 0.006522647 0.0
13 371 0.073212855 0.0
13 372 -0.20731787 0.0
13 375 -0.22431928 0.0
13 378 -0.14367695 0.0
13 382 0.069359556 0.0
13 404 -0.1577996 0.0
13 408 0.19792715 0.0
13 415 -0.06443556 0.0
13 420 0.2181682 0.0
13 424 -0.16662292 0.0
13 429 0.06681999 0.0
13 430 0.008852009 0.0
13 432 0.17732115 0.0
13 433 -0.056288235 0.0
13 434 0.17135216 0.0
13 442 -0.16400896 0.0
13 448 -0.0324661 0.0
13 455 -0.09025117 0.0
13 473 -0.086970866 0.0
13 485 0.106429294 0.0
13 487 0.20951313 0.0
13 491 -0.23149772 0.0
13 516 0.14854038 0.0
13 524 -0.023151819 0.0
13 526 0.16862959 0.0
13 532 -0.17315531 0.0
13 542 0.08101234 0.0
13 546 0.02437075 0.0
13 551 0.122356 0.0
13 559 -0.22966754 0.0
13 566 -0.15344253 0.0
13 578 0.22791794 0.0
13 584 -0.20906217 0.0
13 593 0.11374539 0.0
13 600 -0.14254259 0.0
13 602 0.11220875 0.0
13 604 -0.21061176 0.0
13 605 

...

767 839 -0.14069077 0.0
767 842 -0.003887204 0.0
767 843 -0.050339155 0.0
767 844 -0.08285052 0.0
767 845 0.16069345 0.0
767 847 0.16302004 0.0
767 848 0.07657854 0.0
767 851 -0.11288113 0.0
767 855 -0.0125005115 0.0
767 860 -0.107073665 0.0
767 871 0.07614608 0.0
767 876 -0.01300372 0.0
767 891 -0.00861902 0.0
767 896 -0.16258158 0.0
767 898 -0.115852475 0.0
767 902 -0.057460655 0.0
767 906 0.1949622 0.0
767 912 -0.013532624 0.0
767 913 0.15647623 0.0
767 915 -0.07244289 0.0
767 918 0.21130742 0.0
767 922 0.0454714 0.0
767 925 -0.12531424 0.0
767 933 -0.07174566 0.0
767 935 -0.057396606 0.0
767 950 0.055634324 0.0
767 952 -0.22281712 0.0
767 960 0.03534446 0.0
767 965 -0.2211509 0.0
767 970 0.23593809 0.0
767 975 -0.014099435 0.0
767 977 -0.22082229 0.0
767 979 0.07707167 0.0
767 981 -0.2342513 0.0
767 984 -0.23207422 0.0
767 985 -0.11435967 0.0
767 993 -0.14217559 0.0
767 996 0.21946493 0.0
767 997 0.08395725 0.0
768 2 0.19316353 0.0
768 7 -0.079921305 0.0
768 13 -0.07249452 0.0
768 

771 258 -0.23609464 0.0
771 259 0.1268688 0.0
771 271 -0.21102981 0.0
771 272 -0.099726416 0.0
771 277 0.05368046 0.0
771 278 -0.1320136 0.0
771 281 0.09745741 0.0
771 294 0.16004433 0.0
771 295 -0.11529609 0.0
771 299 -0.09545143 0.0
771 300 -0.20216581 0.0
771 304 -0.018877408 0.0
771 308 0.089268796 0.0
771 313 0.21183407 0.0
771 319 -0.1301197 0.0
771 329 0.17394806 0.0
771 335 0.20098138 0.0
771 336 -0.15159719 0.0
771 345 -0.04535598 0.0
771 350 0.22040042 0.0
771 351 -0.06161823 0.0
771 353 0.051738866 0.0
771 361 -0.1190728 0.0
771 369 0.2121087 0.0
771 380 0.015211851 0.0
771 384 0.02036577 0.0
771 385 -0.027763788 0.0
771 397 0.042745393 0.0
771 403 -0.1777125 0.0
771 408 -0.22374162 0.0
771 410 -0.22801106 0.0
771 423 -0.08623922 0.0
771 425 0.14718334 0.0
771 430 -0.21413532 0.0
771 433 -0.09687428 0.0
771 442 -0.018950526 0.0
771 447 -0.031105528 0.0
771 449 -0.10495394 0.0
771 450 -0.05534622 0.0
771 454 0.23997094 0.0
771 455 0.1523259 0.0
771 462 -0.15453354 0.0
771 469

774 814 -0.09452517 0.0
774 816 0.033016212 0.0
774 825 0.010033256 0.0
774 832 -0.06867674 0.0
774 837 0.21313721 0.0
774 838 -0.0030959044 0.0
774 839 -0.21072666 0.0
774 844 0.23386621 0.0
774 860 0.16745521 0.0
774 863 -0.24168585 0.0
774 864 0.036888573 0.0
774 865 -0.03036245 0.0
774 870 -0.058469538 0.0
774 871 -0.102219254 0.0
774 872 0.19322547 0.0
774 873 -0.039611205 0.0
774 883 -0.08754739 0.0
774 884 0.08022696 0.0
774 889 -0.16764536 0.0
774 900 0.24078466 0.0
774 903 0.23474072 0.0
774 905 0.037725974 0.0
774 913 -0.19929151 0.0
774 919 0.05872483 0.0
774 923 -0.23621847 0.0
774 928 0.17132285 0.0
774 929 0.012578523 0.0
774 948 0.11437281 0.0
774 951 0.16777778 0.0
774 954 0.06247683 0.0
774 958 -0.17603217 0.0
774 967 0.17037743 0.0
774 971 -0.16161141 0.0
774 979 -0.24114898 0.0
774 990 0.12739141 0.0
774 996 0.24256885 0.0
775 7 0.19020277 0.0
775 12 0.058019765 0.0
775 14 -0.06734845 0.0
775 18 0.18225741 0.0
775 20 0.00058795686 0.0
775 22 0.1430718 0.0
775 27 0.02

778 266 -0.033888362 0.0
778 269 0.19572015 0.0
778 270 -0.23735283 0.0
778 276 0.10958741 0.0
778 283 0.08639267 0.0
778 284 0.24237542 0.0
778 301 0.04240363 0.0
778 308 0.22736974 0.0
778 310 -0.10921164 0.0
778 316 -0.12755087 0.0
778 319 -0.1902171 0.0
778 329 0.12964903 0.0
778 332 0.12279768 0.0
778 340 0.010199669 0.0
778 342 0.23442367 0.0
778 364 -0.2043382 0.0
778 367 0.0564886 0.0
778 370 -0.16349544 0.0
778 371 0.08200799 0.0
778 378 -0.2243704 0.0
778 380 -0.16902383 0.0
778 382 -0.08669604 0.0
778 384 0.1503386 0.0
778 413 0.06705753 0.0
778 428 0.15100361 0.0
778 430 -0.11392895 0.0
778 432 0.03263172 0.0
778 436 0.062394828 0.0
778 438 -0.10257306 0.0
778 453 -0.16635145 0.0
778 454 0.15404995 0.0
778 455 0.10440737 0.0
778 461 -0.004746146 0.0
778 462 0.1363419 0.0
778 465 -0.08392817 0.0
778 466 0.032634165 0.0
778 475 0.05309175 0.0
778 484 0.057629295 0.0
778 491 -0.16577011 0.0
778 495 -0.1812296 0.0
778 506 0.011731016 0.0
778 517 -0.06800249 0.0
778 521 -0.04787

781 692 -0.03820302 0.0
781 693 0.15919197 0.0
781 694 -0.19356136 0.0
781 703 0.1264163 0.0
781 705 -0.13050805 0.0
781 707 -0.16302292 0.0
781 713 0.17421332 0.0
781 720 -0.012748721 0.0
781 726 0.1916962 0.0
781 739 -0.24183734 0.0
781 748 0.056621645 0.0
781 749 0.09010907 0.0
781 751 0.05979286 0.0
781 753 -0.1647219 0.0
781 755 -0.21472271 0.0
781 762 -0.21765094 0.0
781 767 -0.07840902 0.0
781 770 0.17673121 0.0
781 772 -0.11376274 0.0
781 773 -0.121299095 0.0
781 776 0.14312677 0.0
781 780 0.23214355 0.0
781 784 0.09975055 0.0
781 786 -0.22500782 0.0
781 792 0.21081963 0.0
781 795 -0.065955244 0.0
781 806 0.021314887 0.0
781 809 -0.12560491 0.0
781 811 -0.09548553 0.0
781 816 0.09653559 0.0
781 822 0.08432929 0.0
781 830 -0.116969705 0.0
781 832 -0.1824727 0.0
781 835 -0.018581377 0.0
781 843 -0.096028924 0.0
781 846 0.15483434 0.0
781 847 0.16194274 0.0
781 849 0.08179203 0.0
781 852 0.22129217 0.0
781 853 0.05378078 0.0
781 857 -0.15385121 0.0
781 858 0.06855368 0.0
781 865 0

In [17]:
to_prune_count

15

In [18]:
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:1}
sess.run(layer_weights_to_prune,feed_dict=test_feed_dict)

100000